# Импорт

In [15]:
import numpy as np
import pandas as pd

from keras import Model, Sequential
from keras.callbacks import EarlyStopping
from keras.layers import Dense, Dropout, Flatten, Input
from tensorflow.keras.utils import to_categorical
import matplotlib.pyplot as plt

ModuleNotFoundError: No module named 'matplotlib'

# Методы:

### Загрузка данных игр в судоку из таблицы

In [2]:
def load_data(nb_train=12000, nb_test=2000, full=False):
    """
    Function to load data in the keras way.
    
    Parameters
    ----------
    nb_train (int): Number of training examples
    nb_test (int): Number of testing examples
    full (bool): If True, whole csv will be loaded, nb_test will be ignored
    
    Returns
    -------
    Xtrain, ytrain (np.array, np.array),
        shapes (nb_train, 9, 9), (nb_train, 9, 9): Training samples
    Xtest, ytest (np.array, np.array), 
        shapes (nb_test, 9, 9), (nb_test, 9, 9): Testing samples
    """
    # if full is true, load the whole dataset
    if full:
        sudokus = pd.read_csv('sudoku.csv').values
    else:
        sudokus = next(
            pd.read_csv('sudoku.csv', chunksize=(nb_train + nb_test))
        ).values
        
    quizzes, solutions = sudokus.T
    flatX = np.array([np.reshape([int(d) for d in flatten_grid], (9, 9))
                      for flatten_grid in quizzes])
    flaty = np.array([np.reshape([int(d) for d in flatten_grid], (9, 9))
                      for flatten_grid in solutions])
    
    return (flatX[:nb_train], flaty[:nb_train]), (flatX[nb_train:], flaty[nb_train:])

### Рассчет точности решений

In [3]:
def diff(grids_true, grids_pred):
    """
    This function shows how well predicted quizzes fit to actual solutions.
    It will store sum of differences for each pair (solution, guess)
    
    Parameters
    ----------
    grids_true (np.array), shape (?, 9, 9): Real solutions to guess in the digit repesentation
    grids_pred (np.array), shape (?, 9, 9): Guesses
    
    Returns
    -------
    diff (np.array), shape (?,): Number of differences for each pair (solution, guess)
    """
    return (grids_true != grids_pred).sum((1, 2))

### Удаление случайных ячеек в решенных играх

In [4]:
def delete_digits(X, n_delet=1):
    """
    This function is used to create sudoku quizzes from solutions
    
    Parameters
    ----------
    X (np.array), shape (?, 9, 9, 9|10): input solutions grids.
    n_delet (integer): max number of digit to suppress from original solutions
    
    Returns
    -------
    grids: np.array of grids to guess in one-hot way. Shape: (?, 9, 9, 10)
    """
    grids = X.argmax(3)  # get the grid in a (9, 9) integer shape
    for grid in grids:
        grid.flat[np.random.randint(0, 81, n_delet)] = 0  # generate blanks (replace = True)
        
    return to_categorical(grids)

### Поиск решения

In [5]:
def batch_smart_solve(grids, solver):
    """
    NOTE : This function is ugly, feel free to optimize the code ...
    
    This function solves quizzes in the "smart" way. 
    It will fill blanks one after the other. Each time a digit is filled, 
    the new grid will be fed again to the solver to predict the next digit. 
    Again and again, until there is no more blank
    
    Parameters
    ----------
    grids (np.array), shape (?, 9, 9): Batch of quizzes to solve (smartly ;))
    solver (keras.model): The neural net solver
    
    Returns
    -------
    grids (np.array), shape (?, 9, 9): Smartly solved quizzes.
    """
    grids = grids.copy()
    for _ in range((grids == 0).sum((1, 2)).max()):
        preds = np.array(solver.predict(to_categorical(grids)))  # get predictions
        probs = preds.max(2).T  # get highest probability for each 81 digit to predict
        values = preds.argmax(2).T + 1  # get corresponding values
        zeros = (grids == 0).reshape((grids.shape[0], 81))  # get blank positions

        for grid, prob, value, zero in zip(grids, probs, values, zeros):
            if any(zero):  # don't try to fill already completed grid
                where = np.where(zero)[0]  # focus on blanks only
                confidence_position = where[prob[zero].argmax()]  # best score FOR A ZERO VALUE (confident blank)
                confidence_value = value[confidence_position]  # get corresponding value
                grid.flat[confidence_position] = confidence_value  # fill digit inplace
    return grids

# Подготовка данных к обучению

In [6]:
load_data(nb_train=12000, nb_test=4000, full=False)

((array([[[0, 0, 4, ..., 2, 0, 9],
          [0, 0, 5, ..., 0, 0, 1],
          [0, 7, 0, ..., 0, 4, 3],
          ...,
          [6, 0, 0, ..., 1, 0, 5],
          [0, 0, 3, ..., 6, 9, 0],
          [0, 4, 2, ..., 3, 0, 0]],
  
         [[0, 4, 0, ..., 0, 5, 0],
          [1, 0, 7, ..., 9, 6, 0],
          [5, 2, 0, ..., 0, 0, 0],
          ...,
          [0, 9, 0, ..., 5, 4, 3],
          [6, 0, 0, ..., 7, 0, 0],
          [2, 5, 0, ..., 1, 0, 0]],
  
         [[6, 0, 0, ..., 3, 8, 4],
          [0, 0, 8, ..., 0, 7, 2],
          [0, 0, 0, ..., 0, 0, 5],
          ...,
          [3, 1, 0, ..., 0, 5, 0],
          [0, 8, 9, ..., 0, 0, 0],
          [5, 0, 2, ..., 1, 9, 0]],
  
         ...,
  
         [[0, 0, 5, ..., 0, 0, 0],
          [8, 7, 9, ..., 0, 1, 5],
          [0, 4, 1, ..., 0, 2, 3],
          ...,
          [9, 0, 8, ..., 0, 5, 0],
          [3, 0, 0, ..., 7, 6, 0],
          [0, 6, 0, ..., 1, 0, 4]],
  
         [[0, 0, 2, ..., 0, 0, 7],
          [8, 0, 9, ..., 0, 0, 0

In [7]:
input_shape = (9, 9, 10)
(_, ytrain), (Xtest, ytest) = load_data()  # We won't use _. We will work directly with ytrain

# one-hot-encoding --> shapes become :
# (?, 9, 9, 10) for Xs
# (?, 9, 9, 9) for ys
Xtrain = to_categorical(ytrain).astype('float32')  # from ytrain cause we will creates quizzes from solusions
Xtest = to_categorical(Xtest).astype('float32')

ytrain = to_categorical(ytrain-1).astype('float32') # (y - 1) because we 
ytest = to_categorical(ytest-1).astype('float32')   # don't want to predict zeros

# Define keras model

In [8]:
model = Sequential()
model.add(Dense(64, activation='relu', input_shape=input_shape))
model.add(Dropout(0.4))
model.add(Dense(64, activation='relu'))
model.add(Dropout(0.4))
model.add(Flatten())

grid = Input(shape=input_shape)  # inputs
features = model(grid)  # commons features

# define one Dense layer for each of the digit we want to predict
digit_placeholders = [
    Dense(9, activation='softmax')(features)
    for i in range(81)
]

solver = Model(grid, digit_placeholders)  # build the whole model
solver.compile(
    optimizer='adam',
    loss='categorical_crossentropy',
    metrics=['accuracy']
)

In [9]:
solver.fit(
    delete_digits(Xtrain, 0),  # we don't delete any digit for now
    [ytrain[:, i, j, :] for i in range(9) for j in range(9)],  # each digit of solution
    batch_size=128,
    epochs=1,  # 1 epoch should be enough for the task
    verbose=1,
)

53/94 [===============>..............] - ETA: 53s - loss: 167.3773 - dense_2_loss: 2.0672 - dense_3_loss: 2.0688 - dense_4_loss: 2.0603 - dense_5_loss: 2.0603 - dense_6_loss: 2.0652 - dense_7_loss: 2.0547 - dense_8_loss: 2.0706 - dense_9_loss: 2.0611 - dense_10_loss: 2.0561 - dense_11_loss: 2.0556 - dense_12_loss: 2.0647 - dense_13_loss: 2.0633 - dense_14_loss: 2.0776 - dense_15_loss: 2.0629 - dense_16_loss: 2.0670 - dense_17_loss: 2.0636 - dense_18_loss: 2.0658 - dense_19_loss: 2.0721 - dense_20_loss: 2.0638 - dense_21_loss: 2.0627 - dense_22_loss: 2.0671 - dense_23_loss: 2.0620 - dense_24_loss: 2.0596 - dense_25_loss: 2.0675 - dense_26_loss: 2.0648 - dense_27_loss: 2.0655 - dense_28_loss: 2.0622 - dense_29_loss: 2.0742 - dense_30_loss: 2.0605 - dense_31_loss: 2.0676 - dense_32_loss: 2.0705 - dense_33_loss: 2.0636 - dense_34_loss: 2.0717 - dense_35_loss: 2.0728 - dense_36_loss: 2.0636 - dense_37_loss: 2.0758 - dense_38_loss: 2.0714 - dense_39_loss: 2.0521 - dense_40_loss: 2.0648 - den

54/94 [================>.............] - ETA: 49s - loss: 166.1876 - dense_2_loss: 2.0525 - dense_3_loss: 2.0539 - dense_4_loss: 2.0475 - dense_5_loss: 2.0447 - dense_6_loss: 2.0498 - dense_7_loss: 2.0386 - dense_8_loss: 2.0558 - dense_9_loss: 2.0467 - dense_10_loss: 2.0422 - dense_11_loss: 2.0413 - dense_12_loss: 2.0501 - dense_13_loss: 2.0478 - dense_14_loss: 2.0627 - dense_15_loss: 2.0482 - dense_16_loss: 2.0523 - dense_17_loss: 2.0494 - dense_18_loss: 2.0520 - dense_19_loss: 2.0570 - dense_20_loss: 2.0504 - dense_21_loss: 2.0470 - dense_22_loss: 2.0531 - dense_23_loss: 2.0484 - dense_24_loss: 2.0456 - dense_25_loss: 2.0527 - dense_26_loss: 2.0498 - dense_27_loss: 2.0502 - dense_28_loss: 2.0487 - dense_29_loss: 2.0599 - dense_30_loss: 2.0458 - dense_31_loss: 2.0523 - dense_32_loss: 2.0567 - dense_33_loss: 2.0480 - dense_34_loss: 2.0562 - dense_35_loss: 2.0595 - dense_36_loss: 2.0471 - dense_37_loss: 2.0606 - dense_38_loss: 2.0583 - dense_39_loss: 2.0387 - dense_40_loss: 2.0500 - den

55/94 [================>.............] - ETA: 47s - loss: 165.5498 - dense_2_loss: 2.0451 - dense_3_loss: 2.0441 - dense_4_loss: 2.0410 - dense_5_loss: 2.0361 - dense_6_loss: 2.0406 - dense_7_loss: 2.0307 - dense_8_loss: 2.0479 - dense_9_loss: 2.0386 - dense_10_loss: 2.0338 - dense_11_loss: 2.0326 - dense_12_loss: 2.0410 - dense_13_loss: 2.0404 - dense_14_loss: 2.0542 - dense_15_loss: 2.0391 - dense_16_loss: 2.0443 - dense_17_loss: 2.0414 - dense_18_loss: 2.0432 - dense_19_loss: 2.0492 - dense_20_loss: 2.0424 - dense_21_loss: 2.0391 - dense_22_loss: 2.0445 - dense_23_loss: 2.0407 - dense_24_loss: 2.0375 - dense_25_loss: 2.0440 - dense_26_loss: 2.0413 - dense_27_loss: 2.0428 - dense_28_loss: 2.0405 - dense_29_loss: 2.0519 - dense_30_loss: 2.0381 - dense_31_loss: 2.0449 - dense_32_loss: 2.0485 - dense_33_loss: 2.0396 - dense_34_loss: 2.0488 - dense_35_loss: 2.0505 - dense_36_loss: 2.0401 - dense_37_loss: 2.0532 - dense_38_loss: 2.0515 - dense_39_loss: 2.0310 - dense_40_loss: 2.0426 - den

56/94 [================>.............] - ETA: 45s - loss: 164.8931 - dense_2_loss: 2.0367 - dense_3_loss: 2.0361 - dense_4_loss: 2.0329 - dense_5_loss: 2.0275 - dense_6_loss: 2.0335 - dense_7_loss: 2.0212 - dense_8_loss: 2.0400 - dense_9_loss: 2.0317 - dense_10_loss: 2.0258 - dense_11_loss: 2.0240 - dense_12_loss: 2.0322 - dense_13_loss: 2.0314 - dense_14_loss: 2.0464 - dense_15_loss: 2.0318 - dense_16_loss: 2.0366 - dense_17_loss: 2.0320 - dense_18_loss: 2.0346 - dense_19_loss: 2.0403 - dense_20_loss: 2.0343 - dense_21_loss: 2.0308 - dense_22_loss: 2.0353 - dense_23_loss: 2.0323 - dense_24_loss: 2.0288 - dense_25_loss: 2.0352 - dense_26_loss: 2.0330 - dense_27_loss: 2.0341 - dense_28_loss: 2.0325 - dense_29_loss: 2.0442 - dense_30_loss: 2.0300 - dense_31_loss: 2.0368 - dense_32_loss: 2.0405 - dense_33_loss: 2.0312 - dense_34_loss: 2.0422 - dense_35_loss: 2.0427 - dense_36_loss: 2.0321 - dense_37_loss: 2.0447 - dense_38_loss: 2.0438 - dense_39_loss: 2.0230 - dense_40_loss: 2.0343 - den

57/94 [=================>............] - ETA: 43s - loss: 164.2123 - dense_2_loss: 2.0280 - dense_3_loss: 2.0287 - dense_4_loss: 2.0230 - dense_5_loss: 2.0190 - dense_6_loss: 2.0248 - dense_7_loss: 2.0128 - dense_8_loss: 2.0312 - dense_9_loss: 2.0229 - dense_10_loss: 2.0172 - dense_11_loss: 2.0157 - dense_12_loss: 2.0244 - dense_13_loss: 2.0227 - dense_14_loss: 2.0376 - dense_15_loss: 2.0244 - dense_16_loss: 2.0287 - dense_17_loss: 2.0255 - dense_18_loss: 2.0269 - dense_19_loss: 2.0313 - dense_20_loss: 2.0247 - dense_21_loss: 2.0242 - dense_22_loss: 2.0266 - dense_23_loss: 2.0227 - dense_24_loss: 2.0207 - dense_25_loss: 2.0257 - dense_26_loss: 2.0258 - dense_27_loss: 2.0247 - dense_28_loss: 2.0250 - dense_29_loss: 2.0366 - dense_30_loss: 2.0215 - dense_31_loss: 2.0283 - dense_32_loss: 2.0331 - dense_33_loss: 2.0228 - dense_34_loss: 2.0333 - dense_35_loss: 2.0331 - dense_36_loss: 2.0251 - dense_37_loss: 2.0363 - dense_38_loss: 2.0370 - dense_39_loss: 2.0135 - dense_40_loss: 2.0257 - den

...

87/94 [==========================>...] - ETA: 6s - loss: 136.2188 - dense_2_loss: 1.6819 - dense_3_loss: 1.6889 - dense_4_loss: 1.6767 - dense_5_loss: 1.6667 - dense_6_loss: 1.6780 - dense_7_loss: 1.6744 - dense_8_loss: 1.6802 - dense_9_loss: 1.6805 - dense_10_loss: 1.6647 - dense_11_loss: 1.6683 - dense_12_loss: 1.6752 - dense_13_loss: 1.6735 - dense_14_loss: 1.6968 - dense_15_loss: 1.6723 - dense_16_loss: 1.6933 - dense_17_loss: 1.6799 - dense_18_loss: 1.6811 - dense_19_loss: 1.6857 - dense_20_loss: 1.6723 - dense_21_loss: 1.6728 - dense_22_loss: 1.6802 - dense_23_loss: 1.6770 - dense_24_loss: 1.6769 - dense_25_loss: 1.6780 - dense_26_loss: 1.6810 - dense_27_loss: 1.6790 - dense_28_loss: 1.6801 - dense_29_loss: 1.6921 - dense_30_loss: 1.6784 - dense_31_loss: 1.6838 - dense_32_loss: 1.6901 - dense_33_loss: 1.6841 - dense_34_loss: 1.6851 - dense_35_loss: 1.6836 - dense_36_loss: 1.6783 - dense_37_loss: 1.6960 - dense_38_loss: 1.6877 - dense_39_loss: 1.6662 - dense_40_loss: 1.6867 - dens

88/94 [===========================>..] - ETA: 5s - loss: 135.1665 - dense_2_loss: 1.6687 - dense_3_loss: 1.6762 - dense_4_loss: 1.6636 - dense_5_loss: 1.6537 - dense_6_loss: 1.6650 - dense_7_loss: 1.6616 - dense_8_loss: 1.6671 - dense_9_loss: 1.6680 - dense_10_loss: 1.6512 - dense_11_loss: 1.6556 - dense_12_loss: 1.6631 - dense_13_loss: 1.6597 - dense_14_loss: 1.6836 - dense_15_loss: 1.6588 - dense_16_loss: 1.6793 - dense_17_loss: 1.6670 - dense_18_loss: 1.6675 - dense_19_loss: 1.6726 - dense_20_loss: 1.6593 - dense_21_loss: 1.6600 - dense_22_loss: 1.6678 - dense_23_loss: 1.6639 - dense_24_loss: 1.6633 - dense_25_loss: 1.6651 - dense_26_loss: 1.6677 - dense_27_loss: 1.6659 - dense_28_loss: 1.6657 - dense_29_loss: 1.6790 - dense_30_loss: 1.6649 - dense_31_loss: 1.6719 - dense_32_loss: 1.6766 - dense_33_loss: 1.6715 - dense_34_loss: 1.6718 - dense_35_loss: 1.6699 - dense_36_loss: 1.6653 - dense_37_loss: 1.6829 - dense_38_loss: 1.6743 - dense_39_loss: 1.6530 - dense_40_loss: 1.6734 - dens

89/94 [===========================>..] - ETA: 4s - loss: 134.1133 - dense_2_loss: 1.6556 - dense_3_loss: 1.6629 - dense_4_loss: 1.6509 - dense_5_loss: 1.6407 - dense_6_loss: 1.6525 - dense_7_loss: 1.6491 - dense_8_loss: 1.6531 - dense_9_loss: 1.6553 - dense_10_loss: 1.6382 - dense_11_loss: 1.6420 - dense_12_loss: 1.6499 - dense_13_loss: 1.6460 - dense_14_loss: 1.6699 - dense_15_loss: 1.6463 - dense_16_loss: 1.6669 - dense_17_loss: 1.6541 - dense_18_loss: 1.6540 - dense_19_loss: 1.6594 - dense_20_loss: 1.6454 - dense_21_loss: 1.6475 - dense_22_loss: 1.6548 - dense_23_loss: 1.6510 - dense_24_loss: 1.6503 - dense_25_loss: 1.6526 - dense_26_loss: 1.6552 - dense_27_loss: 1.6536 - dense_28_loss: 1.6528 - dense_29_loss: 1.6659 - dense_30_loss: 1.6528 - dense_31_loss: 1.6590 - dense_32_loss: 1.6643 - dense_33_loss: 1.6583 - dense_34_loss: 1.6588 - dense_35_loss: 1.6566 - dense_36_loss: 1.6528 - dense_37_loss: 1.6695 - dense_38_loss: 1.6612 - dense_39_loss: 1.6396 - dense_40_loss: 1.6598 - dens

90/94 [===========================>..] - ETA: 3s - loss: 133.0654 - dense_2_loss: 1.6427 - dense_3_loss: 1.6508 - dense_4_loss: 1.6377 - dense_5_loss: 1.6274 - dense_6_loss: 1.6400 - dense_7_loss: 1.6356 - dense_8_loss: 1.6411 - dense_9_loss: 1.6427 - dense_10_loss: 1.6246 - dense_11_loss: 1.6292 - dense_12_loss: 1.6374 - dense_13_loss: 1.6334 - dense_14_loss: 1.6571 - dense_15_loss: 1.6333 - dense_16_loss: 1.6552 - dense_17_loss: 1.6415 - dense_18_loss: 1.6408 - dense_19_loss: 1.6468 - dense_20_loss: 1.6322 - dense_21_loss: 1.6349 - dense_22_loss: 1.6413 - dense_23_loss: 1.6378 - dense_24_loss: 1.6368 - dense_25_loss: 1.6403 - dense_26_loss: 1.6429 - dense_27_loss: 1.6407 - dense_28_loss: 1.6395 - dense_29_loss: 1.6536 - dense_30_loss: 1.6396 - dense_31_loss: 1.6458 - dense_32_loss: 1.6518 - dense_33_loss: 1.6457 - dense_34_loss: 1.6448 - dense_35_loss: 1.6431 - dense_36_loss: 1.6406 - dense_37_loss: 1.6568 - dense_38_loss: 1.6482 - dense_39_loss: 1.6267 - dense_40_loss: 1.6468 - dens

94/94 [==============================] - 117s 888ms/step - loss: 129.2026 - dense_2_loss: 1.5947 - dense_3_loss: 1.6032 - dense_4_loss: 1.5924 - dense_5_loss: 1.5808 - dense_6_loss: 1.5930 - dense_7_loss: 1.5882 - dense_8_loss: 1.5947 - dense_9_loss: 1.5941 - dense_10_loss: 1.5765 - dense_11_loss: 1.5800 - dense_12_loss: 1.5900 - dense_13_loss: 1.5845 - dense_14_loss: 1.6090 - dense_15_loss: 1.5847 - dense_16_loss: 1.6070 - dense_17_loss: 1.5940 - dense_18_loss: 1.5924 - dense_19_loss: 1.5997 - dense_20_loss: 1.5840 - dense_21_loss: 1.5868 - dense_22_loss: 1.5930 - dense_23_loss: 1.5901 - dense_24_loss: 1.5903 - dense_25_loss: 1.5935 - dense_26_loss: 1.5950 - dense_27_loss: 1.5921 - dense_28_loss: 1.5915 - dense_29_loss: 1.6057 - dense_30_loss: 1.5904 - dense_31_loss: 1.5973 - dense_32_loss: 1.6037 - dense_33_loss: 1.5977 - dense_34_loss: 1.5964 - dense_35_loss: 1.5945 - dense_36_loss: 1.5911 - dense_37_loss: 1.6081 - dense_38_loss: 1.5991 - dense_39_loss: 1.5789 - dense_40_loss: 1.599

In [10]:
early_stop = EarlyStopping(patience=2, verbose=1)

i = 1
for nb_epochs, nb_delete in zip(
        [1, 2, 3, 4, 8],  # epochs for each round
        [1, 10, 30, 55]  # digit to pull off
):
    print('Pass n° {} ...'.format(i))
    i += 1
    
    solver.fit(
        delete_digits(Xtrain, nb_delete),  # delete digits from training sample
        [ytrain[:, i, j, :] for i in range(9) for j in range(9)],
        validation_data=(
            delete_digits(Xtrain, nb_delete), # delete same amount of digit from validation sample
            [ytrain[:, i, j, :] for i in range(9) for j in range(9)]),
        batch_size=32,
        epochs=nb_epochs,
        verbose=1,
        callbacks=[early_stop]
    )

Pass n° 1 ...
375/375 [==============================] - 262s 650ms/step - loss: 5.8576 - dense_2_loss: 0.0776 - dense_3_loss: 0.0737 - dense_4_loss: 0.0729 - dense_5_loss: 0.0735 - dense_6_loss: 0.0739 - dense_7_loss: 0.0736 - dense_8_loss: 0.0778 - dense_9_loss: 0.0734 - dense_10_loss: 0.0672 - dense_11_loss: 0.0735 - dense_12_loss: 0.0692 - dense_13_loss: 0.0676 - dense_14_loss: 0.0766 - dense_15_loss: 0.0681 - dense_16_loss: 0.0711 - dense_17_loss: 0.0729 - dense_18_loss: 0.0724 - dense_19_loss: 0.0751 - dense_20_loss: 0.0708 - dense_21_loss: 0.0756 - dense_22_loss: 0.0689 - dense_23_loss: 0.0673 - dense_24_loss: 0.0747 - dense_25_loss: 0.0729 - dense_26_loss: 0.0739 - dense_27_loss: 0.0728 - dense_28_loss: 0.0737 - dense_29_loss: 0.0729 - dense_30_loss: 0.0749 - dense_31_loss: 0.0736 - dense_32_loss: 0.0787 - dense_33_loss: 0.0708 - dense_34_loss: 0.0754 - dense_35_loss: 0.0702 - dense_36_loss: 0.0731 - dense_37_loss: 0.0732 - dense_38_loss: 0.0701 - dense_39_loss: 0.0703 - dense_

Pass n° 2 ...
Epoch 1/2
375/375 [==============================] - 210s 562ms/step - loss: 2.9920 - dense_2_loss: 0.0364 - dense_3_loss: 0.0371 - dense_4_loss: 0.0378 - dense_5_loss: 0.0299 - dense_6_loss: 0.0401 - dense_7_loss: 0.0344 - dense_8_loss: 0.0355 - dense_9_loss: 0.0436 - dense_10_loss: 0.0322 - dense_11_loss: 0.0354 - dense_12_loss: 0.0396 - dense_13_loss: 0.0444 - dense_14_loss: 0.0346 - dense_15_loss: 0.0386 - dense_16_loss: 0.0364 - dense_17_loss: 0.0295 - dense_18_loss: 0.0350 - dense_19_loss: 0.0449 - dense_20_loss: 0.0336 - dense_21_loss: 0.0325 - dense_22_loss: 0.0368 - dense_23_loss: 0.0438 - dense_24_loss: 0.0393 - dense_25_loss: 0.0347 - dense_26_loss: 0.0391 - dense_27_loss: 0.0335 - dense_28_loss: 0.0398 - dense_29_loss: 0.0387 - dense_30_loss: 0.0385 - dense_31_loss: 0.0429 - dense_32_loss: 0.0379 - dense_33_loss: 0.0377 - dense_34_loss: 0.0390 - dense_35_loss: 0.0417 - dense_36_loss: 0.0336 - dense_37_loss: 0.0435 - dense_38_loss: 0.0420 - dense_39_loss: 0.041

Epoch 2/2
375/375 [==============================] - 207s 549ms/step - loss: 1.8780 - dense_2_loss: 0.0275 - dense_3_loss: 0.0230 - dense_4_loss: 0.0235 - dense_5_loss: 0.0210 - dense_6_loss: 0.0225 - dense_7_loss: 0.0274 - dense_8_loss: 0.0216 - dense_9_loss: 0.0231 - dense_10_loss: 0.0231 - dense_11_loss: 0.0220 - dense_12_loss: 0.0281 - dense_13_loss: 0.0277 - dense_14_loss: 0.0210 - dense_15_loss: 0.0220 - dense_16_loss: 0.0262 - dense_17_loss: 0.0242 - dense_18_loss: 0.0282 - dense_19_loss: 0.0262 - dense_20_loss: 0.0268 - dense_21_loss: 0.0222 - dense_22_loss: 0.0247 - dense_23_loss: 0.0283 - dense_24_loss: 0.0265 - dense_25_loss: 0.0186 - dense_26_loss: 0.0214 - dense_27_loss: 0.0186 - dense_28_loss: 0.0185 - dense_29_loss: 0.0258 - dense_30_loss: 0.0256 - dense_31_loss: 0.0259 - dense_32_loss: 0.0283 - dense_33_loss: 0.0284 - dense_34_loss: 0.0239 - dense_35_loss: 0.0197 - dense_36_loss: 0.0276 - dense_37_loss: 0.0237 - dense_38_loss: 0.0219 - dense_39_loss: 0.0234 - dense_40_l

Pass n° 3 ...
Epoch 1/3
375/375 [==============================] - 211s 563ms/step - loss: 3.2569 - dense_2_loss: 0.0370 - dense_3_loss: 0.0365 - dense_4_loss: 0.0429 - dense_5_loss: 0.0347 - dense_6_loss: 0.0369 - dense_7_loss: 0.0343 - dense_8_loss: 0.0498 - dense_9_loss: 0.0339 - dense_10_loss: 0.0355 - dense_11_loss: 0.0361 - dense_12_loss: 0.0378 - dense_13_loss: 0.0351 - dense_14_loss: 0.0410 - dense_15_loss: 0.0395 - dense_16_loss: 0.0381 - dense_17_loss: 0.0493 - dense_18_loss: 0.0393 - dense_19_loss: 0.0386 - dense_20_loss: 0.0400 - dense_21_loss: 0.0445 - dense_22_loss: 0.0424 - dense_23_loss: 0.0355 - dense_24_loss: 0.0389 - dense_25_loss: 0.0446 - dense_26_loss: 0.0456 - dense_27_loss: 0.0469 - dense_28_loss: 0.0455 - dense_29_loss: 0.0361 - dense_30_loss: 0.0420 - dense_31_loss: 0.0393 - dense_32_loss: 0.0466 - dense_33_loss: 0.0439 - dense_34_loss: 0.0391 - dense_35_loss: 0.0387 - dense_36_loss: 0.0430 - dense_37_loss: 0.0347 - dense_38_loss: 0.0378 - dense_39_loss: 0.037

Epoch 2/3
375/375 [==============================] - 174s 466ms/step - loss: 1.6189 - dense_2_loss: 0.0212 - dense_3_loss: 0.0233 - dense_4_loss: 0.0176 - dense_5_loss: 0.0209 - dense_6_loss: 0.0186 - dense_7_loss: 0.0186 - dense_8_loss: 0.0202 - dense_9_loss: 0.0188 - dense_10_loss: 0.0180 - dense_11_loss: 0.0192 - dense_12_loss: 0.0218 - dense_13_loss: 0.0173 - dense_14_loss: 0.0240 - dense_15_loss: 0.0195 - dense_16_loss: 0.0168 - dense_17_loss: 0.0226 - dense_18_loss: 0.0215 - dense_19_loss: 0.0168 - dense_20_loss: 0.0201 - dense_21_loss: 0.0157 - dense_22_loss: 0.0193 - dense_23_loss: 0.0195 - dense_24_loss: 0.0166 - dense_25_loss: 0.0217 - dense_26_loss: 0.0218 - dense_27_loss: 0.0196 - dense_28_loss: 0.0206 - dense_29_loss: 0.0181 - dense_30_loss: 0.0207 - dense_31_loss: 0.0208 - dense_32_loss: 0.0229 - dense_33_loss: 0.0189 - dense_34_loss: 0.0185 - dense_35_loss: 0.0184 - dense_36_loss: 0.0210 - dense_37_loss: 0.0153 - dense_38_loss: 0.0192 - dense_39_loss: 0.0162 - dense_40_l

...

374/375 [============================>.] - ETA: 0s - loss: 1.4318 - dense_2_loss: 0.0167 - dense_3_loss: 0.0174 - dense_4_loss: 0.0142 - dense_5_loss: 0.0211 - dense_6_loss: 0.0185 - dense_7_loss: 0.0186 - dense_8_loss: 0.0168 - dense_9_loss: 0.0142 - dense_10_loss: 0.0178 - dense_11_loss: 0.0198 - dense_12_loss: 0.0177 - dense_13_loss: 0.0162 - dense_14_loss: 0.0150 - dense_15_loss: 0.0183 - dense_16_loss: 0.0201 - dense_17_loss: 0.0202 - dense_18_loss: 0.0187 - dense_19_loss: 0.0170 - dense_20_loss: 0.0157 - dense_21_loss: 0.0200 - dense_22_loss: 0.0200 - dense_23_loss: 0.0159 - dense_24_loss: 0.0209 - dense_25_loss: 0.0161 - dense_26_loss: 0.0163 - dense_27_loss: 0.0177 - dense_28_loss: 0.0127 - dense_29_loss: 0.0168 - dense_30_loss: 0.0165 - dense_31_loss: 0.0134 - dense_32_loss: 0.0180 - dense_33_loss: 0.0133 - dense_34_loss: 0.0187 - dense_35_loss: 0.0192 - dense_36_loss: 0.0183 - dense_37_loss: 0.0187 - dense_38_loss: 0.0179 - dense_39_loss: 0.0205 - dense_40_loss: 0.0187 - dens

375/375 [==============================] - ETA: 0s - loss: 1.4315 - dense_2_loss: 0.0167 - dense_3_loss: 0.0174 - dense_4_loss: 0.0141 - dense_5_loss: 0.0211 - dense_6_loss: 0.0184 - dense_7_loss: 0.0186 - dense_8_loss: 0.0168 - dense_9_loss: 0.0142 - dense_10_loss: 0.0178 - dense_11_loss: 0.0198 - dense_12_loss: 0.0176 - dense_13_loss: 0.0161 - dense_14_loss: 0.0150 - dense_15_loss: 0.0184 - dense_16_loss: 0.0201 - dense_17_loss: 0.0202 - dense_18_loss: 0.0187 - dense_19_loss: 0.0170 - dense_20_loss: 0.0159 - dense_21_loss: 0.0199 - dense_22_loss: 0.0199 - dense_23_loss: 0.0159 - dense_24_loss: 0.0211 - dense_25_loss: 0.0160 - dense_26_loss: 0.0163 - dense_27_loss: 0.0176 - dense_28_loss: 0.0128 - dense_29_loss: 0.0167 - dense_30_loss: 0.0165 - dense_31_loss: 0.0134 - dense_32_loss: 0.0180 - dense_33_loss: 0.0132 - dense_34_loss: 0.0187 - dense_35_loss: 0.0192 - dense_36_loss: 0.0182 - dense_37_loss: 0.0187 - dense_38_loss: 0.0181 - dense_39_loss: 0.0204 - dense_40_loss: 0.0190 - dens

375/375 [==============================] - 84s 224ms/step - loss: 1.4315 - dense_2_loss: 0.0167 - dense_3_loss: 0.0174 - dense_4_loss: 0.0141 - dense_5_loss: 0.0211 - dense_6_loss: 0.0184 - dense_7_loss: 0.0186 - dense_8_loss: 0.0168 - dense_9_loss: 0.0142 - dense_10_loss: 0.0178 - dense_11_loss: 0.0198 - dense_12_loss: 0.0176 - dense_13_loss: 0.0161 - dense_14_loss: 0.0150 - dense_15_loss: 0.0184 - dense_16_loss: 0.0201 - dense_17_loss: 0.0202 - dense_18_loss: 0.0187 - dense_19_loss: 0.0170 - dense_20_loss: 0.0159 - dense_21_loss: 0.0199 - dense_22_loss: 0.0199 - dense_23_loss: 0.0159 - dense_24_loss: 0.0211 - dense_25_loss: 0.0160 - dense_26_loss: 0.0163 - dense_27_loss: 0.0176 - dense_28_loss: 0.0128 - dense_29_loss: 0.0167 - dense_30_loss: 0.0165 - dense_31_loss: 0.0134 - dense_32_loss: 0.0180 - dense_33_loss: 0.0132 - dense_34_loss: 0.0187 - dense_35_loss: 0.0192 - dense_36_loss: 0.0182 - dense_37_loss: 0.0187 - dense_38_loss: 0.0181 - dense_39_loss: 0.0204 - dense_40_loss: 0.0190

Epoch 3/4
375/375 [==============================] - 79s 212ms/step - loss: 1.0584 - dense_2_loss: 0.0130 - dense_3_loss: 0.0136 - dense_4_loss: 0.0126 - dense_5_loss: 0.0166 - dense_6_loss: 0.0147 - dense_7_loss: 0.0139 - dense_8_loss: 0.0154 - dense_9_loss: 0.0146 - dense_10_loss: 0.0101 - dense_11_loss: 0.0135 - dense_12_loss: 0.0143 - dense_13_loss: 0.0087 - dense_14_loss: 0.0132 - dense_15_loss: 0.0134 - dense_16_loss: 0.0161 - dense_17_loss: 0.0115 - dense_18_loss: 0.0127 - dense_19_loss: 0.0132 - dense_20_loss: 0.0134 - dense_21_loss: 0.0156 - dense_22_loss: 0.0123 - dense_23_loss: 0.0131 - dense_24_loss: 0.0153 - dense_25_loss: 0.0131 - dense_26_loss: 0.0144 - dense_27_loss: 0.0143 - dense_28_loss: 0.0109 - dense_29_loss: 0.0110 - dense_30_loss: 0.0084 - dense_31_loss: 0.0148 - dense_32_loss: 0.0120 - dense_33_loss: 0.0098 - dense_34_loss: 0.0155 - dense_35_loss: 0.0123 - dense_36_loss: 0.0100 - dense_37_loss: 0.0140 - dense_38_loss: 0.0123 - dense_39_loss: 0.0145 - dense_40_lo

Epoch 4/4
375/375 [==============================] - 115s 308ms/step - loss: 0.9613 - dense_2_loss: 0.0131 - dense_3_loss: 0.0139 - dense_4_loss: 0.0149 - dense_5_loss: 0.0124 - dense_6_loss: 0.0085 - dense_7_loss: 0.0121 - dense_8_loss: 0.0108 - dense_9_loss: 0.0142 - dense_10_loss: 0.0089 - dense_11_loss: 0.0109 - dense_12_loss: 0.0089 - dense_13_loss: 0.0097 - dense_14_loss: 0.0094 - dense_15_loss: 0.0167 - dense_16_loss: 0.0090 - dense_17_loss: 0.0113 - dense_18_loss: 0.0115 - dense_19_loss: 0.0135 - dense_20_loss: 0.0127 - dense_21_loss: 0.0140 - dense_22_loss: 0.0141 - dense_23_loss: 0.0083 - dense_24_loss: 0.0116 - dense_25_loss: 0.0105 - dense_26_loss: 0.0156 - dense_27_loss: 0.0112 - dense_28_loss: 0.0091 - dense_29_loss: 0.0153 - dense_30_loss: 0.0083 - dense_31_loss: 0.0130 - dense_32_loss: 0.0119 - dense_33_loss: 0.0097 - dense_34_loss: 0.0114 - dense_35_loss: 0.0113 - dense_36_loss: 0.0120 - dense_37_loss: 0.0124 - dense_38_loss: 0.0117 - dense_39_loss: 0.0136 - dense_40_l

In [11]:
pyplot.title('Learning Curves')
pyplot.xlabel('Epoch')
pyplot.ylabel('Cross Entropy')
pyplot.plot(solver.history['loss'], label='train')
pyplot.plot(solver.history['val_loss'], label='val')
pyplot.legend()
pyplot.show()

NameError: name 'pyplot' is not defined